# Exploratory Data Anaysis with SQL

I was tasked with discovering information by performing SQL inquiries, these were prompted queries to demonstrate proficiency in running SQL queries and subqueries.

In [2]:
%load_ext sql

In [3]:
import csv, sqlite3

con = sqlite3.connect("my_data1.db")
cur = con.cursor()

In [5]:
%sql sqlite:///my_data1.db

In [6]:
import pandas as pd
df = pd.read_csv("https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBM-DS0321EN-SkillsNetwork/labs/module_2/data/Spacex.csv")
df.to_sql("SPACEXTBL", con, if_exists='replace', index=False,method="multi")

101

Removing any blank rows from the table

In [7]:
%sql create table SPACEXTABLE as select * from SPACEXTBL where Date is not null

 * sqlite:///my_data1.db
Done.


[]

First I looked for the names of the unique launch sites  in the space mission

In [8]:
%sql select DISTINCT "Launch_Site" from SPACEXTABLE

 * sqlite:///my_data1.db
Done.


[('CCAFS LC-40',), ('VAFB SLC-4E',), ('KSC LC-39A',), ('CCAFS SLC-40',)]

Next I looked for records where launch sites begin with the string 'CCA' 

In [9]:
%sql select * from SPACEXTABLE where "Launch_Site" LIKE 'CCA%' limit 5

 * sqlite:///my_data1.db
Done.


[('2010-06-04', '18:45:00', 'F9 v1.0  B0003', 'CCAFS LC-40', 'Dragon Spacecraft Qualification Unit', 0, 'LEO', 'SpaceX', 'Success', 'Failure (parachute)'),
 ('2010-12-08', '15:43:00', 'F9 v1.0  B0004', 'CCAFS LC-40', 'Dragon demo flight C1, two CubeSats, barrel of Brouere cheese', 0, 'LEO (ISS)', 'NASA (COTS) NRO', 'Success', 'Failure (parachute)'),
 ('2012-05-22', '7:44:00', 'F9 v1.0  B0005', 'CCAFS LC-40', 'Dragon demo flight C2', 525, 'LEO (ISS)', 'NASA (COTS)', 'Success', 'No attempt'),
 ('2012-10-08', '0:35:00', 'F9 v1.0  B0006', 'CCAFS LC-40', 'SpaceX CRS-1', 500, 'LEO (ISS)', 'NASA (CRS)', 'Success', 'No attempt'),
 ('2013-03-01', '15:10:00', 'F9 v1.0  B0007', 'CCAFS LC-40', 'SpaceX CRS-2', 677, 'LEO (ISS)', 'NASA (CRS)', 'Success', 'No attempt')]

Next I looked for  the total payload mass carried by boosters launched by NASA (CRS)

In [10]:
%sql select SUM(PAYLOAD_MASS__KG_) from SPACEXTABLE where "Customer" like 'NASA (CRS)%'

 * sqlite:///my_data1.db
Done.


[(48213,)]

Next I looked for the average payload mass carried by booster version F9 v1.1


In [11]:
%sql select AVG(PAYLOAD_MASS__KG_) from SPACEXTABLE where "Booster_Version" LIKE 'F9 v1.1%'

 * sqlite:///my_data1.db
Done.


[(2534.6666666666665,)]

Looking for the date when the first succesful landing outcome in ground pad was acheived.

In [12]:
%sql select MIN("Date") from SPACEXTABLE where "Landing_Outcome"='Success (ground pad)'

 * sqlite:///my_data1.db
Done.


[('2015-12-22',)]

Looking for the total number of successful and failure mission outcomes

In [13]:
%sql select "Mission_Outcome", count("Mission_Outcome") from SPACEXTABLE GROUP BY "Mission_Outcome" 

 * sqlite:///my_data1.db
Done.


[('Failure (in flight)', 1),
 ('Success', 98),
 ('Success ', 1),
 ('Success (payload status unclear)', 1)]

Looking for the records which will display the month names, failure landing_outcomes in drone ship ,booster versions, launch_site for the months in year 2015.

In [14]:
%sql SELECT CASE SUBSTR("Date", 6, 2)WHEN '01' THEN 'January'WHEN '02' THEN 'February'WHEN '03' THEN 'March'WHEN '04' THEN 'April'WHEN '05' THEN 'May'WHEN '06' THEN 'June'WHEN '07' THEN 'July'WHEN '08' THEN 'August'WHEN '09' THEN 'September'WHEN '10' THEN 'October'WHEN '11' THEN 'November'WHEN '12' THEN 'December'ELSE 'Unknown'  END AS month,"Landing_Outcome"='Failure (drone ship)',"Booster_Version","Launch_Site"FROM SPACEXTABLE WHERE SUBSTR("Date", 0, 5) = '2015';

 * sqlite:///my_data1.db
Done.


[('January', 1, 'F9 v1.1 B1012', 'CCAFS LC-40'),
 ('February', 0, 'F9 v1.1 B1013', 'CCAFS LC-40'),
 ('March', 0, 'F9 v1.1 B1014', 'CCAFS LC-40'),
 ('April', 1, 'F9 v1.1 B1015', 'CCAFS LC-40'),
 ('April', 0, 'F9 v1.1 B1016', 'CCAFS LC-40'),
 ('June', 0, 'F9 v1.1 B1018', 'CCAFS LC-40'),
 ('December', 0, 'F9 FT B1019', 'CCAFS LC-40')]

Here I attempted to rank the landing outcomes by multiple criterion, and within a specific date range. 

In [15]:
%sql select "Landing_Outcome",count("Landing_Outcome") from SPACEXTABLE where "Date" between 20100604 and 20170320 group by "Landing_Outcome" order by 2 desc


 * sqlite:///my_data1.db
Done.


[('Success (drone ship)', 12),
 ('No attempt', 12),
 ('Success (ground pad)', 8),
 ('Failure (drone ship)', 5),
 ('Controlled (ocean)', 4),
 ('Uncontrolled (ocean)', 2),
 ('Precluded (drone ship)', 1)]